<div style="font-family: Arial, Helvetica, sans-serif;">
    <div style="display: flex;padding-top: 20px">
        <div><strong>Course:</strong> Statistical Learning</div>
    </div>
    <div style="display: flex;padding-top: 20px">
        <div style="padding-right: 10px;"><strong>Class:</strong> 22CNTTh</div>
        <div></div>
    </div>
    <div style="display: flex;padding-top: 20px">
        <div style="padding-right: 10px;"><strong>Group:</strong> ...</div>
    </div>
    <div>
        <div style="display: flex;padding-top: 20px">
            <div style="padding-right: 10px;"><strong>Members:</strong></div>
            <div></div>
        </div>
        <table style="font-size: 15px; display:flex;padding-top: 20px">
            <tr>
                <th>No.</th>
                <th>Student ID</th>
                <th>Name</th>
            </tr>
            <tr>
                <td>1</td>
                <td> 22127004 </td>
                <td style="text-align:left;">Trình Cao An</td>
            </tr>
            <tr>
                <td>2</td>
                <td>22127014</td>
                <td style="text-align:left;">Nguyễn Kim Anh</td>
            </tr>
            <tr>
                <td>3</td>
                <td> 22127214 </td>
                <td style="text-align:left;">Võ Thị Kim Khôi</td>
            </tr>
        </table>
    </div>
    <div style="font-size: 25px ;font-weight: 800; text-align: center;padding-top: 20px;">FINAL PROJECT</div>
    <div style="font-size: 20px ;font-weight: 800; text-align: center;padding-top: 20px;">VIETNAMESE STOCKINSIGHT - MODEL FINTUNING - XLM-Roberta</div>
</div>

In [ ]:
# Drive
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# Importing packages

In [ ]:
!pip install seqeval
!pip install evaluate

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import json
import re

from collections import Counter
from datasets import Dataset, DatasetDict, load_from_disk, concatenate_datasets
from transformers import (
    AutoConfig,
    AutoModelForTokenClassification,
    AutoTokenizer,
    DataCollatorForTokenClassification,
    HfArgumentParser,
    PretrainedConfig,
    PreTrainedTokenizerFast,
    Trainer,
    TrainingArguments,
    set_seed,
)

import torch
from tqdm import tqdm

# from seqeval.metrics import classification_report, precision_score, recall_score, f1_score
# import evaluate

# Loading datasets

In [ ]:
path = 'drive/MyDrive/statlearning/phobert_tokenized_datasets'
raw_datasets1 = DatasetDict({
    "train": load_from_disk(f"{path}/train"),
    "validation": load_from_disk(f"{path}/validation"),
    "test": load_from_disk(f"{path}/test")
})
raw_datasets1

/usr/local/lib/python3.11/dist-packages/datasets/table.py:1421: FutureWarning: promote has been superseded by promote_options='default'.
  table = cls._concat_blocks(blocks, axis=0)


DatasetDict({
    train: Dataset({
        features: ['tokens', 'labels', 'original_text', 'source', 'labels_id', 'input_ids', 'token_type_ids', 'attention_mask'],
        num_rows: 84996
    })
    validation: Dataset({
        features: ['tokens', 'labels', 'original_text', 'source', 'labels_id', 'input_ids', 'token_type_ids', 'attention_mask'],
        num_rows: 10625
    })
    test: Dataset({
        features: ['tokens', 'labels', 'original_text', 'source', 'labels_id', 'input_ids', 'token_type_ids', 'attention_mask'],
        num_rows: 10625
    })
})

In [ ]:
path = 'drive/MyDrive/statlearning/xlm_roberta_tokenized_datasets'
raw_datasets2 = DatasetDict({
    "train": load_from_disk(f"{path}/train"),
    "validation": load_from_disk(f"{path}/validation"),
    "test": load_from_disk(f"{path}/test")
})
raw_datasets2

DatasetDict({
    train: Dataset({
        features: ['tokens', 'labels', 'original_text', 'source', 'labels_id', 'input_ids', 'attention_mask'],
        num_rows: 84996
    })
    validation: Dataset({
        features: ['tokens', 'labels', 'original_text', 'source', 'labels_id', 'input_ids', 'attention_mask'],
        num_rows: 10625
    })
    test: Dataset({
        features: ['tokens', 'labels', 'original_text', 'source', 'labels_id', 'input_ids', 'attention_mask'],
        num_rows: 10625
    })
})

# Knowledge Base Construction

Convert to `pandas Dataframe`

In [ ]:
all_phobert_chunks = concatenate_datasets([
    raw_datasets1["train"],
    raw_datasets1["validation"],
    raw_datasets1["test"]])

all_phobert_df = all_phobert_chunks.to_pandas().reset_index(drop=True)
all_phobert_df.head()

tokens  \
0  Nhóm có liên_quan đến Beston tăng sở_hữu tại V...   
1  Lãnh_đạo May_Sông_Hồng muốn rút sạch vốn sau k...   
2  Cổ_phiếu nào kéo VN-Index bật lại sau cú rơi h...   
3  Cổ_phiếu HNG có khả_năng bị huỷ niêm_yết bắt_b...   
4  Quỹ đầu_tư mạnh_tay mua cổ phiếu.Trong tuần qu...   

                                              labels  \
0  [-100, 28, 28, 28, 28, 28, 28, 28, 28, 28, 20,...   
1  [-100, 28, 20, 21, 21, 28, 28, 28, 28, 28, 28,...   
2  [-100, 28, 28, 28, 28, 28, 28, 28, 28, 28, 28,...   
3  [-100, 28, 20, 28, 28, 28, 28, 28, 28, 28, 28,...   
4  [-100, 28, 28, 28, 28, 28, 28, 28, 28, 28, 28,...   

                                       original_text  \
0  Nhóm có liên quan đến Beston tăng sở hữu tại V...   
1  Lãnh đạo May Sông Hồng muốn rút sạch vốn sau k...   
2  Cổ phiếu nào kéo VN-Index bật lại sau cú rơi h...   
3  Cổ phiếu HNG có khả năng bị hủy niêm yết bắt b...   
4  Quỹ đầu tư mạnh tay mua cổ phiếu.Trong tuần qu...   

                                              source  \
0  https://vietstock.vn/2025/03/nhom-co-lien-quan...   
1  https://vietstock.vn/2025/03/lanh-dao-may-song...   
2  https://vietstock.vn/2025/04/co-phieu-nao-keo-...   
3  https://vietstock.vn/2024/02/co-phieu-hng-co-k...   
4  https://vietstock.vn/2025/02/quy-dau-tu-manh-t...   

                                           labels_id  \
0  [28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 2...   
1  [28, 28, 28, 28, 28, 28, 28, 28, 28, 20, 28, 2...   
2  [28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 2...   
3  [28, 28, 28, 28, 28, 28, 28, 28, 28, 20, 21, 2...   
4  [28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 2...   

                                           input_ids  \
0  [0, 2131, 10, 314, 30, 19833, 4258, 128, 692, ...   
1  [0, 2768, 16785, 16218, 1892, 202, 951, 1024, ...   
2  [0, 11481, 142, 1300, 6082, 2340, 44, 53, 1486...   
3  [0, 11481, 32117, 10, 259, 45, 3374, 2784, 288...   
4  [0, 4096, 158, 7143, 188, 862, 42243, 26115, 9...   

                                      token_type_ids  \
0   [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
1  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
2      [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]   
3  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   
4  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...   

                                      attention_mask  
0   [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]  
1  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...  
2      [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]  
3  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...  
4  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...

In [ ]:
all_xlmr_chunks = concatenate_datasets([
    raw_datasets2["train"],
    raw_datasets2["validation"],
    raw_datasets2["test"]])

all_xlmr_df = all_xlmr_chunks.to_pandas().reset_index(drop=True)
all_xlmr_df.head()

/usr/local/lib/python3.11/dist-packages/datasets/table.py:1421: FutureWarning: promote has been superseded by promote_options='default'.
  table = cls._concat_blocks(blocks, axis=0)


tokens  \
0  [Nhóm, có, liên_quan, đến, Beston, tăng, sở_hữ...   
1  [Lãnh_đạo, May_Sông_Hồng, muốn, rút, sạch, vốn...   
2  [Cổ_phiếu, nào, kéo, VN-Index, bật, lại, sau, ...   
3  [Cổ_phiếu, HNG, có, khả_năng, bị, huỷ, niêm_yế...   
4  [Quỹ, đầu_tư, mạnh_tay, mua, cổ, phiếu.Trong, ...   

                                              labels  \
0  [-100, 28, 28, 28, -100, -100, -100, 28, 28, -...   
1  [-100, 28, -100, -100, -100, 28, -100, -100, -...   
2  [-100, 28, -100, -100, -100, 28, 28, 28, -100,...   
3  [-100, 28, -100, -100, -100, 28, -100, 28, 28,...   
4  [-100, 28, -100, 28, -100, -100, -100, 28, -10...   

                                       original_text  \
0  Nhóm có liên quan đến Beston tăng sở hữu tại V...   
1  Lãnh đạo May Sông Hồng muốn rút sạch vốn sau k...   
2  Cổ phiếu nào kéo VN-Index bật lại sau cú rơi h...   
3  Cổ phiếu HNG có khả năng bị hủy niêm yết bắt b...   
4  Quỹ đầu tư mạnh tay mua cổ phiếu.Trong tuần qu...   

                                              source  \
0  https://vietstock.vn/2025/03/nhom-co-lien-quan...   
1  https://vietstock.vn/2025/03/lanh-dao-may-song...   
2  https://vietstock.vn/2025/04/co-phieu-nao-keo-...   
3  https://vietstock.vn/2024/02/co-phieu-hng-co-k...   
4  https://vietstock.vn/2025/02/quy-dau-tu-manh-t...   

                                           labels_id  \
0  [28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 2...   
1  [28, 28, 28, 28, 28, 28, 28, 28, 28, 20, 28, 2...   
2  [28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 2...   
3  [28, 28, 28, 28, 28, 28, 28, 28, 28, 20, 21, 2...   
4  [28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 28, 2...   

                                           input_ids  \
0  [0, 233934, 524, 8151, 454, 13722, 19, 1885, 1...   
1  [0, 211289, 454, 18643, 77248, 4347, 454, 294,...   
2  [0, 84538, 454, 19379, 63513, 3941, 44577, 870...   
3  [0, 84538, 454, 19379, 63513, 572, 8066, 524, ...   
4  [0, 10022, 149631, 2494, 454, 18, 11479, 14463...   

                                      attention_mask  
0  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...  
1  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...  
2  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...  
3  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...  
4  [1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, ...

## Loading models

In [ ]:
from huggingface_hub import notebook_login

notebook_login() #token tương ứng với acc có repo

In [ ]:
hub_model_id1 = "AnTrinh/my-phobert-ner"

model1 = AutoModelForTokenClassification.from_pretrained(hub_model_id1)
tokenizer1 = AutoTokenizer.from_pretrained(hub_model_id1, use_fast=True)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/1.88k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/538M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.20k [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/895k [00:00<?, ?B/s]

bpe.codes:   0%|          | 0.00/1.14M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/22.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/167 [00:00<?, ?B/s]

In [ ]:
hub_model_id2 = "PuppetLover/XLM-Roberta_NER"

model2 = AutoModelForTokenClassification.from_pretrained(hub_model_id2)
tokenizer2 = AutoTokenizer.from_pretrained(hub_model_id2, use_fast=True)

config.json:   0%|          | 0.00/1.87k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.11G [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/1.18k [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.07M [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/17.1M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/280 [00:00<?, ?B/s]

In [ ]:
id2label1 = model1.config.id2label
label2id1 = model1.config.label2id

id2label2 = model2.config.id2label
label2id2 = model2.config.label2id

In [ ]:
list_labels = list(id2label2.values())

list_labels

['B-COMPANY',
 'I-COMPANY',
 'B-EVENT',
 'I-EVENT',
 'B-FIN_IND',
 'I-FIN_IND',
 'B-LAW',
 'I-LAW',
 'B-LOC',
 'I-LOC',
 'B-MBS',
 'I-MBS',
 'B-NUM',
 'I-NUM',
 'B-PERSON',
 'I-PERSON',
 'B-PRICE_ACTION',
 'I-PRICE_ACTION',
 'B-RISK',
 'I-RISK',
 'B-STOCK',
 'I-STOCK',
 'B-STRATEGY',
 'I-STRATEGY',
 'B-TIME',
 'I-TIME',
 'B-TITLE',
 'I-TITLE',
 'O']

In [ ]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model1.to(device)
model2.to(device)

XLMRobertaForTokenClassification(
  (roberta): XLMRobertaModel(
    (embeddings): XLMRobertaEmbeddings(
      (word_embeddings): Embedding(250002, 768, padding_idx=1)
      (position_embeddings): Embedding(514, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): XLMRobertaEncoder(
      (layer): ModuleList(
        (0-11): 12 x XLMRobertaLayer(
          (attention): XLMRobertaAttention(
            (self): XLMRobertaSdpaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): XLMRobertaSelfOutput(
              (dense): Linear(in_features=768, out_features=768

In [ ]:
eval_args = TrainingArguments(
    output_dir="/content/drive/MyDrive/statlearning/ner_results",
    per_device_eval_batch_size=16,
    report_to="none",
)

In [ ]:
trainer1 = Trainer(model=model1, args=eval_args, data_collator=DataCollatorForTokenClassification(tokenizer1))
trainer2 = Trainer(model=model2, args=eval_args, data_collator=DataCollatorForTokenClassification(tokenizer2))

## Connect to SQLite and prepare tables

In [ ]:
import sqlite3

conn = sqlite3.connect('/content/drive/MyDrive/statlearning/stock_insights.db')
c = conn.cursor()

# Articles
c.execute('''
CREATE TABLE IF NOT EXISTS Articles (
    article_id   INTEGER PRIMARY KEY AUTOINCREMENT,
    title        TEXT,
    source_url   TEXT,
    publish_date TEXT,
    content      TEXT NOT NULL
);
''')

# Tạo bảng Entities
c.execute('''
CREATE TABLE IF NOT EXISTS Entities (
    entity_id    INTEGER PRIMARY KEY AUTOINCREMENT,
    article_id   INTEGER NOT NULL,
    entity_text  TEXT NOT NULL,
    entity_type  TEXT NOT NULL,
    confidence   TEXT CHECK(confidence IN ('high','medium')),
    detected_by  TEXT CHECK(detected_by IN ('ensemble','phoBERT_only','xlmr_only')),
    FOREIGN KEY(article_id) REFERENCES Articles(article_id) ON DELETE CASCADE
);
''')

# Tạo bảng Sentences
c.execute('''
CREATE TABLE IF NOT EXISTS Sentences (
    sentence_id     INTEGER PRIMARY KEY AUTOINCREMENT,
    article_id      INTEGER NOT NULL,
    sentence_text   TEXT NOT NULL,14
    sentiment_label TEXT,
    sentiment_score REAL,
    FOREIGN KEY(article_id) REFERENCES Articles(article_id) ON DELETE CASCADE
);
''')

conn.commit()
conn.close()
print("DB and tables created successfully.")

DB and tables created successfully.


In [ ]:
def insert_article(c, source_url, content):
    c.execute(
        "INSERT OR IGNORE INTO Articles(title, source_url, publish_date, content) VALUES (?, ?, ?, ?)",
        ("", source_url, "", content)
    )
    c.execute("SELECT article_id FROM Articles WHERE source_url=?", (source_url,))
    result = c.fetchone()
    return result[0] if result else None

In [ ]:
def insert_entities(c, art_id, both, set1, set2):
    for text, label in both:
        c.execute("""INSERT INTO Entities(article_id, entity_text, entity_type, confidence, detected_by) VALUES (?,?,?,?,?)""",
                  (art_id, text, label, 'high', 'ensemble'))
    for text, label in set1 - both:
        c.execute("""INSERT INTO Entities(article_id, entity_text, entity_type, confidence, detected_by) VALUES (?,?,?,?,?)""",
                  (art_id, text, label, 'medium', 'phoBERT_only'))
    for text, label in set2 - both:
        c.execute("""INSERT INTO Entities(article_id, entity_text, entity_type, confidence, detected_by) VALUES (?,?,?,?,?)""",
                  (art_id, text, label, 'medium', 'xlmr_only'))

In [ ]:
def insert_sentences(c, art_id, content):
    sents = [s.strip() for s in re.split(r'(?<=[.!?])\s+', content) if s]
    for sent in sents:
        c.execute("""INSERT INTO Sentences(article_id, sentence_text) VALUES (?,?)""", (art_id, sent))

## Utility to extract entities from token‐level predictions

In [ ]:
def extract_entities(tokens, preds, id2label):
    entities, cur = [], None
    for i, (tok, p) in enumerate(zip(tokens, preds)):
        lbl = id2label[p]
        if lbl.startswith("B-"):
            if cur: entities.append(cur)
            cur = {"text": tok, "start": i, "end": i+1, "label": lbl[2:]}
        elif lbl.startswith("I-") and cur and lbl[2:] == cur["label"]:
            cur["text"] += " " + tok
            cur["end"] = i+1
        else:
            if cur: entities.append(cur); cur = None
    if cur: entities.append(cur)
    return entities

## Predict for all datasets

In [ ]:
def process_article(source_url, df_phobert, df_xlmr, trainer1, trainer2, id2label1, id2label2, c):
    # Get chunk of article
    phobert_chunks = df_phobert[df_phobert['source'] == source_url].reset_index(drop=True)
    xlmr_chunks = df_xlmr[df_xlmr['source'] == source_url].reset_index(drop=True)

    # Get content of articles
    content = phobert_chunks['original_text'].iloc[0]

    # Insert/get article_id 
    art_id = insert_article(c, source_url, content)
    if not art_id:
        print(f"Warning: Could not retrieve article_id for {source_url}")
        return
    hf_phobert = Dataset.from_pandas(phobert_chunks)
    hf_xlmr = Dataset.from_pandas(xlmr_chunks)

    # Predict
    out1 = trainer1.predict(hf_phobert)
    out2 = trainer2.predict(hf_xlmr)
    preds1 = np.argmax(out1.predictions, axis=2)
    preds2 = np.argmax(out2.predictions, axis=2)

    # Tổng hợp
    phobert_entities = []
    xlmr_entities = []
    for idx, row in phobert_chunks.iterrows():
        toks = row['tokens']
        pred1_list = preds1[idx].tolist() if idx < len(preds1) else [-100] * len(toks)
        phobert_entities += extract_entities(toks, pred1_list, id2label1)
    for idx, row in xlmr_chunks.iterrows():
        toks = row['tokens']
        pred2_list = preds2[idx].tolist() if idx < len(preds2) else [-100] * len(toks)
        xlmr_entities += extract_entities(toks, pred2_list, id2label2)

    set1 = {(e['text'], e['label']) for e in phobert_entities}
    set2 = {(e['text'], e['label']) for e in xlmr_entities}
    both = set1 & set2

    # Save entities
    insert_entities(c, art_id, both, set1, set2)

    # Save sentences
    insert_sentences(c, art_id, content)

In [ ]:
conn = sqlite3.connect('/content/drive/MyDrive/statlearning/stock_insights.db')
c = conn.cursor()
try:
    for source_url in tqdm(all_phobert_df['source'].unique(), desc="Articles"):
        try:
            process_article(source_url, all_phobert_df, all_xlmr_df, trainer1, trainer2, id2label1, id2label2, c)
            conn.commit()
        except sqlite3.Error as e:
            print(f"Database error for article {source_url}: {e}")
            conn.rollback()
        except Exception as e:
            print(f"Error processing article {source_url}: {e}")
            conn.rollback()
finally:
    conn.close()
    print("Database connection closed.")

Articles:   0%|          | 0/6450 [00:00<?, ?it/s]

Articles:   0%|          | 1/6450 [00:00<1:21:45,  1.31it/s]

Articles:   0%|          | 2/6450 [00:00<45:00,  2.39it/s]  

Articles:   0%|          | 3/6450 [00:01<31:39,  3.39it/s]

Articles:   0%|          | 4/6450 [00:01<29:19,  3.66it/s]

...

Articles: 100%|█████████▉| 6447/6450 [25:39<00:00,  4.23it/s]

Articles: 100%|█████████▉| 6448/6450 [25:39<00:00,  3.49it/s]

Articles: 100%|█████████▉| 6449/6450 [25:40<00:00,  3.69it/s]

Articles: 100%|██████████| 6450/6450 [25:40<00:00,  4.19it/s]

Database connection closed.
